In [20]:
import os
import json
import pg8000
import nest_asyncio
nest_asyncio.apply()
import uuid
import sqlalchemy
import pandas as pd
from ragas import evaluate
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.output_parsers import StrOutputParser
from sqlalchemy import text
from dotenv import load_dotenv
from langchain.schema import Document

from langchain_groq import ChatGroq
from langchain.document_loaders import DataFrameLoader
from google.cloud.sql.connector import Connector, IPTypes
from langchain_openai import ChatOpenAI, OpenAIEmbeddings

from ragas.testset import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context

In [2]:
EVAL_PARENT_DIR = "evaluation/"
EVAL_TESTSET_DIR = f"{EVAL_PARENT_DIR}/testset"
EVAL_RESULTS_DIR = f"{EVAL_PARENT_DIR}/results"

In [3]:
load_dotenv()

True

In [4]:
## load the API Keys
os.environ['HF_TOKEN']=os.getenv("HF_TOKEN")
os.environ['OPENAI_API_KEY']=os.getenv("OPENAI_API_KEY")
os.environ['GROQ_API_KEY']=os.getenv("GROQ_API_KEY")
os.environ["TOKENIZERS_PARALLELISM"] = "false"

## Langfuse
os.environ['LANGFUSE_PUBLIC_KEY']=os.getenv("LANGFUSE_PUBLIC_KEY")
os.environ['LANGFUSE_SECRET_KEY']=os.getenv("LANGFUSE_SECRET_KEY")
os.environ['LANGFUSE_HOST']=os.getenv("LANGFUSE_HOST")

## Postgres DB
instance_connection_name = os.getenv("INSTANCE_CONNECTION_NAME")
db_user = os.getenv("DB_USER")  
db_pass = os.getenv("DB_PASS")  
db_name = os.getenv("DB_NAME")  

In [11]:
REVIEW_TABLE = "ecom-chat-437005.ecom_chat.review"
META_TABLE = "ecom-chat-437005.ecom_chat.meta"

In [12]:
product_asins = [
    "B00000IV35", "0975277324", "8499000606", "B00000IZJB", "1933054395", 
    "0976990709", "B00000IZKX", "B00000ISC5", "B00001ZWV7", "B00005O6B7", 
    "B0000205XI", "B00000DMD2", "B00000IV95", "B00000IV34", "B00005BZKD", 
    "1932855785", "B00000JBMZ", "B00004W3Y4", "B00004TFLB", "160169024X", 
    "B00000JIVS", "B00004YO15", "2914849656", "B00004NKLB", "B00000DMER", 
    "B000062SPJ", "B00000IZOU", "B00003008E", "076245945X", "B000050B3H"
]

## Connect Postgres

In [6]:
def connect_with_db() -> sqlalchemy.engine.base.Engine:
    ip_type = IPTypes.PRIVATE if os.getenv("PRIVATE_IP") else IPTypes.PUBLIC
    connector = Connector()
    def getconn() -> pg8000.dbapi.Connection:
        conn: pg8000.dbapi.Connection = connector.connect(
            instance_connection_name,
            "pg8000",
            user=db_user,
            password=db_pass,
            db=db_name,
            ip_type=ip_type,
        )
        return conn
    pool = sqlalchemy.create_engine(
        "postgresql+pg8000://",
        creator=getconn,
    )
    return pool

In [7]:
engine = connect_with_db()

In [9]:
def fetch_data(parent_asin):
    with engine.begin() as connection:
        try:
            query = text(f"""
                        SELECT parent_asin, asin, helpful_vote, timestamp, verified_purchase, title, text
                        FROM userreviews ur 
                        WHERE ur.parent_asin = '{parent_asin}';""")
            result = connection.execute(query)
            review_df = pd.DataFrame(result.fetchall(), columns=result.keys())

            query = text(f"""
                     SELECT parent_asin, main_category, title, average_rating, rating_number, features, description, price, store, categories, details
                     FROM metadata md 
                     WHERE md.parent_asin = '{parent_asin}';
                """)
            result = connection.execute(query)
            meta_df = pd.DataFrame(result.fetchall(), columns=result.keys())

            return review_df, meta_df
        except Exception as e: print(e)

In [14]:
def metadata_node(meta_df):
    meta_llm = ChatGroq(model_name="llama-3.1-8b-instant")

    modified_details = meta_df['details'].astype(str).str.replace('{', '[')
    
    # Answer question
    meta_system_prompt =( 
        f'''
        You are a great Data Interpreter and Summarizer. Read the Product Meta Data sent to you and Produce it in 500 words.
        
        Meta Data:
        main_category: {(meta_df.at[0,'main_category'])}
        title: {(meta_df.at[0, 'title'])}
        average_rating: {(meta_df.at[0, 'average_rating'])}
        rating_number: {(meta_df.at[0, 'rating_number'])}
        features: {(meta_df.at[0, 'features'])}
        description: {(meta_df.at[0, 'description'])}
        price: {(meta_df.at[0, 'price'])}
        store: {(meta_df.at[0, 'store'])}
        categories: {(meta_df.at[0, 'categories'])}	
        details: {(modified_details.at[0])}

        Return in a proper format:
        main_category: Same 
        title: Same
        average_rating: Same
        rating_number: Same
        features: Summarize	
        description: Summarize
        price: Same
        store: Same	
        categories: Same	
        details: Same/Summarize where necessary	

        Do not answer any user question, just provide the meta data
        '''
    )

    meta_system_prompt = meta_system_prompt.replace('{', '{{').replace('}', '}}')

    meta_qa_prompt = ChatPromptTemplate.from_messages(
                    [
                        ("system", meta_system_prompt),
                    ]
                )
    parser = StrOutputParser()
    meta_chain = meta_qa_prompt | meta_llm | parser

    try:
        # Meta Summary
        meta_results = meta_chain.invoke({'input': ''})
        meta_results = Document(page_content=meta_results, metadata={"source": "Metadata"})
        
    except Exception as error:
        print(error)
        content = "Metadata: Unable to generate result"
        meta_results = Document(page_content=content, metadata={"source": "Metadata"})

    return meta_results

In [31]:
review_df, meta_df = fetch_data(product_asins[1])

In [37]:
# Load the Reviews
review_df = review_df[review_df['text'].notna()]
loader = DataFrameLoader(review_df) 
review_docs = loader.load()
review_docs.insert(0, metadata_node(meta_df))

In [16]:
# generator with openai models
generator_llm = ChatOpenAI(model="gpt-4o-mini")
critic_llm = ChatOpenAI(model="gpt-4o")
embeddings = OpenAIEmbeddings(model="text-embedding-3-small")

In [25]:
def get_ragas_testset(doc, with_debugging_logs=False):    
    generator = TestsetGenerator.from_langchain(
        generator_llm,
        critic_llm,
        embeddings,
    )
    
    # generate testset
    testset = generator.generate_with_langchain_docs(
        doc, 
        test_size= 4,
        distributions={simple: 0.5, reasoning: 0.25, multi_context: 0.25},
        with_debugging_logs = with_debugging_logs,
    )
    return testset

In [27]:
def transform_ragas_testset_df(testset):
    ragas_test_df = testset.to_pandas()
    ragas_test_df.drop(columns=['metadata', 'episode_done'], inplace=True)
    return ragas_test_df

In [18]:
hash_table = {asin: str(uuid.uuid4()) for asin in product_asins}

In [22]:
with open('../artifact/product_uuids.json', 'w') as json_file:
    json.dump(hash_table, json_file, indent=4)

In [41]:
for idx, asin in enumerate(product_asins):
    if idx >=25:
        review_df, meta_df = fetch_data(asin)

        # Load the Reviews
        review_df = review_df[review_df['text'].notna()]
        loader = DataFrameLoader(review_df) 
        review_docs = loader.load()
        review_docs.insert(0, metadata_node(meta_df))

        try:
            print(f"Generating Test Data for {asin}...")
            testset = get_ragas_testset(review_docs[:20] if len(review_docs) > 20 else review_docs)
            test_df = transform_ragas_testset_df(testset)
            test_df.to_parquet(f'../{EVAL_TESTSET_DIR}/{hash_table[asin]}.parquet')
        except Exception as e:
            print(f'Error occurred while processing {asin}: {e}')
            continue

Generating Test Data for B000062SPJ...


Filename and doc_id are the same for all nodes.                 
Generating: 100%|██████████| 4/4 [00:42<00:00, 10.58s/it]


Generating Test Data for B00000IZOU...


Filename and doc_id are the same for all nodes.                 
Generating: 100%|██████████| 4/4 [00:55<00:00, 13.93s/it]


Generating Test Data for B00003008E...


Filename and doc_id are the same for all nodes.                 
Generating: 100%|██████████| 4/4 [00:46<00:00, 11.50s/it]


Generating Test Data for 076245945X...


Filename and doc_id are the same for all nodes.                 
Generating: 100%|██████████| 4/4 [00:37<00:00,  9.37s/it]


Generating Test Data for B000050B3H...


Filename and doc_id are the same for all nodes.                 
Generating: 100%|██████████| 4/4 [01:16<00:00, 19.10s/it]
